In [1]:
import pandas as pd
df = pd.read_csv('elephantidae.csv')
df.head()

id       observed_on_string observed_on           time_observed_at  \
0   4126      July 25, 2009 01:58  2009-07-25  2009-07-25 08:58:00 +0000   
1   9636               2010-03-10  2010-03-10                        NaN   
2  13158               2011-03-17  2011-03-17                        NaN   
3  16344  November 30, 2007 15:52  2007-11-30  2007-11-30 20:52:00 +0000   
4  16346  November 29, 2007 17:03  2007-11-29  2007-11-29 22:03:00 +0000   

                    time_zone quality_grade      license  \
0  Pacific Time (US & Canada)      research  CC-BY-NC-ND   
1  Pacific Time (US & Canada)      research          CC0   
2  Pacific Time (US & Canada)      research          CC0   
3  Eastern Time (US & Canada)      research        CC-BY   
4  Eastern Time (US & Canada)      research        CC-BY   

                                           image_url  \
0  https://inaturalist-open-data.s3.amazonaws.com...   
1  https://inaturalist-open-data.s3.amazonaws.com...   
2  https://inaturalist-open-data.s3.amazonaws.com...   
3  https://inaturalist-open-data.s3.amazonaws.com...   
4  https://inaturalist-open-data.s3.amazonaws.com...   

                                         description   latitude  ...  \
0  Blogged here: <a href="http://godutchbaby.blog... -19.502735  ...   
1  I do not have a good telephoto! I was futzing ... -25.020364  ...   
2                                                NaN -25.067835  ...   
3                                                NaN -17.946449  ...   
4  Location approximate to between Maun & Planet ... -20.253259  ...   

         common_name  iconic_taxon_name  taxon_id taxon_kingdom_name  \
0  Savannah Elephant           Mammalia     43694           Animalia   
1  Savannah Elephant           Mammalia     43694           Animalia   
2  Savannah Elephant           Mammalia     43694           Animalia   
3  Savannah Elephant           Mammalia     43694           Animalia   
4  Savannah Elephant           Mammalia     43694           Animalia   

  taxon_phylum_name  taxon_class_name taxon_order_name taxon_family_name  \
0          Chordata          Mammalia      Proboscidea      Elephantidae   
1          Chordata          Mammalia      Proboscidea      Elephantidae   
2          Chordata          Mammalia      Proboscidea      Elephantidae   
3          Chordata          Mammalia      Proboscidea      Elephantidae   
4          Chordata          Mammalia      Proboscidea      Elephantidae   

  taxon_genus_name  taxon_species_name  
0        Loxodonta  Loxodonta africana  
1        Loxodonta  Loxodonta africana  
2        Loxodonta  Loxodonta africana  
3        Loxodonta  Loxodonta africana  
4        Loxodonta  Loxodonta africana  

[5 rows x 27 columns]

In [2]:
print(df.columns)
print("\n")
print(len(df.index))

Index(['id', 'observed_on_string', 'observed_on', 'time_observed_at',
       'time_zone', 'quality_grade', 'license', 'image_url', 'description',
       'latitude', 'longitude', 'positional_accuracy',
       'public_positional_accuracy', 'geoprivacy', 'taxon_geoprivacy',
       'coordinates_obscured', 'scientific_name', 'common_name',
       'iconic_taxon_name', 'taxon_id', 'taxon_kingdom_name',
       'taxon_phylum_name', 'taxon_class_name', 'taxon_order_name',
       'taxon_family_name', 'taxon_genus_name', 'taxon_species_name'],
      dtype='object')


12904


In [3]:
elephants_species = df['taxon_species_name'].dropna().unique()
for nom in elephants_species:
    print(nom)

Loxodonta africana
Elephas maximus
Loxodonta cyclotis


African savanna elephant (Loxodonta africana): Endangered (IUCN)

Asian elephant (Elephas maximus): Endangered (IUCN)

African forest elephant (Loxodonta cyclotis): critically endangered (IUCN)

In [17]:
print(len(df.index))
elephants = df.dropna(subset=['taxon_species_name'])
print(len(elephants.index))
elephants['observed_on'] = pd.to_datetime(elephants['observed_on'], format='%Y-%m-%d')

def assign_season(date):
    month = date.month
    if month in [12, 1, 2]:  
        return 'winter'
    elif month in [6, 7, 8]: 
        return 'summer'
    elif month in [9, 10, 11]:
        return 'autumn'
    else :
        return "spring"

elephants['saison'] = elephants['observed_on'].apply(assign_season)

elephants_season = elephants[elephants['saison'].isin(['winter', 'summer'])]
print(len(elephants_season.index))
elephants_clean = elephants_season.dropna(subset=['latitude', 'longitude'])
print(len(elephants_clean.index))

12904
12652
6864
6838


C:\Users\mimic\AppData\Local\Temp\ipykernel_23732\1252773330.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  elephants['observed_on'] = pd.to_datetime(elephants['observed_on'], format='%Y-%m-%d')
C:\Users\mimic\AppData\Local\Temp\ipykernel_23732\1252773330.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  elephants['saison'] = elephants['observed_on'].apply(assign_season)


In [18]:
import folium

# Fonction pour tracer les observations sur une carte
def create_map(data, season, species_colors):
    m = folium.Map(location=[0, 0], zoom_start=2)
    season_data = data[data['saison'] == season]
    for _, row in season_data.iterrows():
        species = row['taxon_species_name']
        color = species_colors.get(species, 'gray')  # Couleur par défaut si non spécifié
        folium.CircleMarker(
            location=[row['latitude'], row['longitude']],
            radius=5,
            color=color,
            fill=True,
            fill_opacity=0.7
        ).add_to(m)
    return m

# Couleurs pour les espèces
species_colors = {
    'Loxodonta africana': 'blue',
    'Elephas maximus': 'green',
    'Loxodonta cyclotis': 'red'
}

# Créer les cartes pour l'hiver et l'été
carte_hiver = create_map(elephants_clean, 'winter', species_colors)
carte_été = create_map(elephants_clean, 'summer', species_colors)

# Afficher les cartes
display(carte_hiver)
display(carte_été)